# Perceptron implementation

This code demonstrates basic implementation of a perceptron using NumPy and Pandas packages.

In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from functions import *

#print(help(generate_data))
#print(help(get_weighted_sum))
#print(help(sigmoid))
#print(help(network_init))

In [2]:
n_features = 3
m_examples = 15
data = generate_data(m_examples, n_features, seed=15)
print('Features and labels matrix:\n---------------------------\n')
print(data, '\n\n---------------------------')
X = data.drop(columns=['targets']).values
Y = data['targets'].values
print(f'Number of features: {X.shape[1]}')
print(f'Number of training examples: {X.shape[0]}')

Features and labels matrix:
---------------------------

          x0        x1        x2  targets
0   0.692743  0.815817  0.344407        1
1   0.044838  0.571597  0.146245        0
2   0.718771  0.345357  0.457010        1
3   0.975938  0.781466  0.843790        0
4   0.555114  0.941621  0.018326        1
5   0.889184  0.389758  0.231740        1
6   0.534394  0.944690  0.330998        1
7   0.908621  0.467332  0.967288        0
8   0.764227  0.783354  0.361527        0
9   0.587788  0.248549  0.800139        1
10  0.258527  0.672610  0.075345        1
11  0.246870  0.358120  0.172055        1
12  0.260295  0.201803  0.039764        0
13  0.342869  0.468250  0.417349        1
14  0.899524  0.088874  0.623966        1 

---------------------------
Number of features: 3
Number of training examples: 15


In [3]:
weights, bias = network_init(n_features, seed=18)
print('Initial network parameters:')
for i in range(len(weights)):
    print(f'w{i} = {weights[i]}')
print(f'b = {bias}')

Initial network parameters:
w0 = 0.39930576921757277
w1 = 0.7174146792882161
w2 = 0.2808233280360034
b = 0


# Forward propagation

In this section, forward propagation through the perceptron is performed using initialized weights and bias.

In [4]:
def forward_prop(X, weights, bias):
    weighted_sums = []
    Y_hat = []
    for i in range(m_examples):
        example = X[i,:]
        weighted_sum = get_weighted_sum(example, weights, bias)
        weighted_sums.append(weighted_sum)
        y_hat = sigmoid(weighted_sum)
        Y_hat.append(y_hat)
    return Y_hat, weighted_sums

Y_hat, weighted_sums = forward_prop(X, weights, bias)
initial_pass = pd.DataFrame({'weighted_sum':weighted_sums, 'Y':Y, 'Y_hat':Y_hat})
print('Initial forward propagation results:\n---------------------------\n')
print(initial_pass)

Initial forward propagation results:
---------------------------

    weighted_sum  Y     Y_hat
0       0.958613  1  0.722844
1       0.469046  0  0.615158
2       0.663112  1  0.659959
3       1.187289  0  0.766256
4       0.902340  1  0.711430
5       0.699753  1  0.668133
6       0.984073  1  0.727916
7       0.969725  0  0.725065
8       0.968675  0  0.724855
9       0.637718  1  0.654237
10      0.606930  1  0.647240
11      0.403815  1  0.599604
12      0.259881  0  0.564607
13      0.590040  1  0.643374
14      0.598169  1  0.645237


## Cross-entropy loss

In [33]:
def cross_entropy(Y, Y_hat):
    losses = []
    for i in range(len(Y)):
        y = Y[i]
        y_hat = Y_hat[i]
        cross_entropy_loss = -(y*np.log10(y_hat) + (1-y)*np.log10(1-y_hat))
        losses.append(cross_entropy_loss)
    cost = sum(losses) / len(losses)
    return losses, cost
losses, cost = cross_entropy(Y, Y_hat)

initial_pass_with_cost = initial_pass.copy()
initial_pass_with_cost.drop(columns=['weighted_sum'], inplace=True)
initial_pass_with_cost['c-e loss'] = losses
print('Initial forward propagation results with losses:\n---------------------------\n')
print(initial_pass_with_cost, '\n\n---------------------------')
print(f'Total epoch cost: {cost:.4f}')

Initial forward propagation results with losses:
---------------------------

    Y     Y_hat  c-e loss
0   1  0.722844  0.324562
1   0  0.615158  0.954922
2   1  0.659959  0.415577
3   0  0.766256  1.453528
4   1  0.711430  0.340478
5   1  0.668133  0.403268
6   1  0.727916  0.317570
7   0  0.725065  1.291220
8   0  0.724855  1.290458
9   1  0.654237  0.424285
10  1  0.647240  0.435038
11  1  0.599604  0.511486
12  0  0.564607  0.831506
13  1  0.643374  0.441028
14  1  0.645237  0.438137 

---------------------------
Total epoch cost: 0.6582


## Network training

Training a neural network consists of several steps:
1. Initialize weights and bias  
2. Perform forward propagation and calculate epoch/batch cost  
3. Update weights and bias in back-propagation  
4. Repeat steps 2 and 3 until convergence

### Initialize training parameters

In [46]:
epoch = 100
alpha = 0.01

In [53]:
def gradient_descent(X, Y, Y_hat, weights, bias, alpha=0.01):
    m = X.shape[0]
    dj_dw = 0
    dj_db = 0    
    for i in range(m):
        y = Y[i]
        y_hat = Y_hat[i]
        x = X[i]
        dj_dw_i = (y_hat - y) * x
        dj_db_i = (y_hat - y)
        dj_dw += dj_dw_i
        dj_db += dj_db_i
    dj_dw = dj_dw / m
    dj_db = dj_db / m
    print(dj_dw)
    print(dj_db)
    updated_weights = weights - alpha * dj_dw
    updated_bias = bias - alpha * dj_db
    return updated_weights, updated_bias

In [54]:
updated_weights, updated_bias = gradient_descent(X, Y, Y_hat, weights, bias)
#print(updated_weights)
#print(updated_bias)

[0.01755775 0.020284   0.03712931]
0.005061040226606087


In [44]:
def perceptron_train(X, Y, alpha=alpha, epoch=epoch, seed_val=18):
    weights, bias = network_init(X.shape[1], seed=seed_val)
    cost_acc = []
    for i in range(epoch):
        Y_hat_epoch, _ = forward_prop(X, weights, bias)
        _, cost = cross_entropy(Y, Y_hat_epoch)
        cost_acc.append(cost)
        print(f'Epoch {i+1} cost: {cost}\n-----------------------------------')
        weights, bias = gradient_descent(X, Y, Y_hat_epoch, weights, bias, alpha)
    return weights, bias, cost_acc

In [45]:
final_weights, final_bias, cost_acc = perceptron_train(X, Y)

Epoch 1 cost: 0.658204262010536
-----------------------------------
Epoch 2 cost: 0.6581830421928739
-----------------------------------
Epoch 3 cost: 0.6581618994414158
-----------------------------------
Epoch 4 cost: 0.6581408332010991
-----------------------------------
Epoch 5 cost: 0.6581198429208732
-----------------------------------
Epoch 6 cost: 0.6580989280536725
-----------------------------------
Epoch 7 cost: 0.6580780880563901
-----------------------------------
Epoch 8 cost: 0.6580573223898483
-----------------------------------
Epoch 9 cost: 0.6580366305187754
-----------------------------------
Epoch 10 cost: 0.658016011911776
-----------------------------------
Epoch 11 cost: 0.6579954660413064
-----------------------------------
Epoch 12 cost: 0.657974992383647
-----------------------------------
Epoch 13 cost: 0.6579545904188773
-----------------------------------
Epoch 14 cost: 0.6579342596308491
-----------------------------------
Epoch 15 cost: 0.657913999507160

Epoch 1720 cost: 0.6410253936067143
-----------------------------------
Epoch 1721 cost: 0.6410180208603974
-----------------------------------
Epoch 1722 cost: 0.6410106498984326
-----------------------------------
Epoch 1723 cost: 0.6410032807202016
-----------------------------------
Epoch 1724 cost: 0.6409959133250864
-----------------------------------
Epoch 1725 cost: 0.6409885477124695
-----------------------------------
Epoch 1726 cost: 0.6409811838817338
-----------------------------------
Epoch 1727 cost: 0.6409738218322616
-----------------------------------
Epoch 1728 cost: 0.6409664615634365
-----------------------------------
Epoch 1729 cost: 0.6409591030746419
-----------------------------------
Epoch 1730 cost: 0.6409517463652611
-----------------------------------
Epoch 1731 cost: 0.6409443914346784
-----------------------------------
Epoch 1732 cost: 0.6409370382822779
-----------------------------------
Epoch 1733 cost: 0.6409296869074441
----------------------------

Epoch 3418 cost: 0.6306520254785686
-----------------------------------
Epoch 3419 cost: 0.6306469700225671
-----------------------------------
Epoch 3420 cost: 0.6306419155980131
-----------------------------------
Epoch 3421 cost: 0.6306368622045986
-----------------------------------
Epoch 3422 cost: 0.630631809842016
-----------------------------------
Epoch 3423 cost: 0.6306267585099568
-----------------------------------
Epoch 3424 cost: 0.6306217082081136
-----------------------------------
Epoch 3425 cost: 0.630616658936179
-----------------------------------
Epoch 3426 cost: 0.6306116106938451
-----------------------------------
Epoch 3427 cost: 0.6306065634808047
-----------------------------------
Epoch 3428 cost: 0.6306015172967504
-----------------------------------
Epoch 3429 cost: 0.6305964721413755
-----------------------------------
Epoch 3430 cost: 0.6305914280143725
-----------------------------------
Epoch 3431 cost: 0.6305863849154345
------------------------------

Epoch 5048 cost: 0.623589972907847
-----------------------------------
Epoch 5049 cost: 0.6235862631975938
-----------------------------------
Epoch 5050 cost: 0.6235825541447363
-----------------------------------
Epoch 5051 cost: 0.6235788457491069
-----------------------------------
Epoch 5052 cost: 0.6235751380105383
-----------------------------------
Epoch 5053 cost: 0.6235714309288628
-----------------------------------
Epoch 5054 cost: 0.6235677245039132
-----------------------------------
Epoch 5055 cost: 0.6235640187355221
-----------------------------------
Epoch 5056 cost: 0.6235603136235226
-----------------------------------
Epoch 5057 cost: 0.623556609167747
-----------------------------------
Epoch 5058 cost: 0.6235529053680288
-----------------------------------
Epoch 5059 cost: 0.6235492022242001
-----------------------------------
Epoch 5060 cost: 0.6235454997360947
-----------------------------------
Epoch 5061 cost: 0.6235417979035452
------------------------------

Epoch 6612 cost: 0.6184977809178477
-----------------------------------
Epoch 6613 cost: 0.6184949266583478
-----------------------------------
Epoch 6614 cost: 0.6184920728527286
-----------------------------------
Epoch 6615 cost: 0.6184892195008902
-----------------------------------
Epoch 6616 cost: 0.6184863666027332
-----------------------------------
Epoch 6617 cost: 0.6184835141581567
-----------------------------------
Epoch 6618 cost: 0.6184806621670618
-----------------------------------
Epoch 6619 cost: 0.6184778106293479
-----------------------------------
Epoch 6620 cost: 0.6184749595449157
-----------------------------------
Epoch 6621 cost: 0.6184721089136654
-----------------------------------
Epoch 6622 cost: 0.6184692587354969
-----------------------------------
Epoch 6623 cost: 0.6184664090103106
-----------------------------------
Epoch 6624 cost: 0.618463559738007
-----------------------------------
Epoch 6625 cost: 0.6184607109184866
-----------------------------

...

Epoch 92765 cost: 0.595332721253335
-----------------------------------
Epoch 92766 cost: 0.5953327202518669
-----------------------------------
Epoch 92767 cost: 0.59533271925048
-----------------------------------
Epoch 92768 cost: 0.5953327182491744
-----------------------------------
Epoch 92769 cost: 0.5953327172479503
-----------------------------------
Epoch 92770 cost: 0.5953327162468073
-----------------------------------
Epoch 92771 cost: 0.5953327152457457
-----------------------------------
Epoch 92772 cost: 0.5953327142447654
-----------------------------------
Epoch 92773 cost: 0.5953327132438663
-----------------------------------
Epoch 92774 cost: 0.5953327122430484
-----------------------------------
Epoch 92775 cost: 0.5953327112423121
-----------------------------------
Epoch 92776 cost: 0.5953327102416566
-----------------------------------
Epoch 92777 cost: 0.5953327092410827
-----------------------------------
Epoch 92778 cost: 0.5953327082405901
-----------------

Epoch 94431 cost: 0.5953311606639199
-----------------------------------
Epoch 94432 cost: 0.5953311597891404
-----------------------------------
Epoch 94433 cost: 0.595331158914432
-----------------------------------
Epoch 94434 cost: 0.5953311580397946
-----------------------------------
Epoch 94435 cost: 0.5953311571652283
-----------------------------------
Epoch 94436 cost: 0.595331156290733
-----------------------------------
Epoch 94437 cost: 0.5953311554163087
-----------------------------------
Epoch 94438 cost: 0.5953311545419552
-----------------------------------
Epoch 94439 cost: 0.5953311536676724
-----------------------------------
Epoch 94440 cost: 0.5953311527934612
-----------------------------------
Epoch 94441 cost: 0.5953311519193204
-----------------------------------
Epoch 94442 cost: 0.5953311510452508
-----------------------------------
Epoch 94443 cost: 0.595331150171252
-----------------------------------
Epoch 94444 cost: 0.5953311492973243
-----------------

Epoch 96214 cost: 0.5953297084550582
-----------------------------------
Epoch 96215 cost: 0.5953297076981026
-----------------------------------
Epoch 96216 cost: 0.5953297069412087
-----------------------------------
Epoch 96217 cost: 0.595329706184376
-----------------------------------
Epoch 96218 cost: 0.5953297054276045
-----------------------------------
Epoch 96219 cost: 0.5953297046708947
-----------------------------------
Epoch 96220 cost: 0.5953297039142461
-----------------------------------
Epoch 96221 cost: 0.595329703157659
-----------------------------------
Epoch 96222 cost: 0.595329702401133
-----------------------------------
Epoch 96223 cost: 0.5953297016446687
-----------------------------------
Epoch 96224 cost: 0.5953297008882654
-----------------------------------
Epoch 96225 cost: 0.5953297001319237
-----------------------------------
Epoch 96226 cost: 0.5953296993756434
-----------------------------------
Epoch 96227 cost: 0.5953296986194243
-----------------

Epoch 98031 cost: 0.5953284295529514
-----------------------------------
Epoch 98032 cost: 0.5953284288997016
-----------------------------------
Epoch 98033 cost: 0.5953284282465048
-----------------------------------
Epoch 98034 cost: 0.5953284275933608
-----------------------------------
Epoch 98035 cost: 0.5953284269402699
-----------------------------------
Epoch 98036 cost: 0.595328426287232
-----------------------------------
Epoch 98037 cost: 0.5953284256342469
-----------------------------------
Epoch 98038 cost: 0.5953284249813146
-----------------------------------
Epoch 98039 cost: 0.5953284243284355
-----------------------------------
Epoch 98040 cost: 0.5953284236756091
-----------------------------------
Epoch 98041 cost: 0.5953284230228358
-----------------------------------
Epoch 98042 cost: 0.5953284223701153
-----------------------------------
Epoch 98043 cost: 0.5953284217174477
-----------------------------------
Epoch 98044 cost: 0.5953284210648332
---------------

Epoch 99572 cost: 0.595327483190623
-----------------------------------
Epoch 99573 cost: 0.5953274826140763
-----------------------------------
Epoch 99574 cost: 0.5953274820375766
-----------------------------------
Epoch 99575 cost: 0.5953274814611234
-----------------------------------
Epoch 99576 cost: 0.5953274808847172
-----------------------------------
Epoch 99577 cost: 0.5953274803083574
-----------------------------------
Epoch 99578 cost: 0.5953274797320443
-----------------------------------
Epoch 99579 cost: 0.595327479155778
-----------------------------------
Epoch 99580 cost: 0.5953274785795583
-----------------------------------
Epoch 99581 cost: 0.5953274780033855
-----------------------------------
Epoch 99582 cost: 0.5953274774272592
-----------------------------------
Epoch 99583 cost: 0.5953274768511798
-----------------------------------
Epoch 99584 cost: 0.5953274762751468
-----------------------------------
Epoch 99585 cost: 0.5953274756991608
----------------